In [10]:
!pip install --upgrade ffmpeg-python
!pip install ultralytics
!pip install roboflow
from IPython.display import clear_output
clear_output()

In [11]:
import glob
import natsort
import ffmpeg
import numpy as np
from ipywidgets import interact
from matplotlib import pyplot as plt
import os

In [15]:
!rm -rf frames
os.mkdir('frames')

In [17]:
try:
  out = (
      
        ffmpeg
        .input("/content/subsample.mp4")
        .filter('fps', fps='29.98')
        .output('frames/frame%d.jpg', 
            start_number=0)
        .overwrite_output()
        .run(quiet=True)
    
)
except ffmpeg.Error as e:
      print(e.stderr)






In [18]:
input = natsort.natsorted(glob.glob('/content/frames/*.jpg'))

In [19]:
from ultralytics import YOLO

model = YOLO('yolov8n.pt')
# results = model.train(data=r"C:\Users\Koumeyl\Projects\Koumeyl-YOLOv8_Computer_Vision_Project\data.yaml")  # train the model
# results = model.val()  # evaluate model performance on the validation set





In [20]:
os.mkdir('datasets')
os.chdir('datasets')
from roboflow import Roboflow
rf = Roboflow(api_key="nPzcB6fsMdL9RBSvpvJ2")
project = rf.workspace("roboflow-universe-projects").project("soccer-players-ckbru")
dataset = project.version(16).download("yolov8")
%cd {/content}

loading Roboflow workspace...
loading Roboflow project...
Dependency ultralytics<=8.0.20 is required but found version=8.0.25, to fix: `pip install ultralytics<=8.0.20`


Extracting Dataset Version Zip to Soccer-Players-16 in yolov8:: 100%|██████████| 312/312 [00:00<00:00, 923.10it/s]

[Errno 2] No such file or directory: '{/content}'
/content


In [21]:
!ls 

Soccer-Players-16


In [23]:
results = model.train(data="/content/datasets/Soccer-Players-16/data.yaml", epochs=5, plots=True)  # train the model

Ultralytics YOLOv8.0.25 🚀 Python-3.8.10 torch-1.13.1+cu116 CPU
yolo/engine/trainer: task=detect, mode=train, model=yolov8n.yaml, data=/content/datasets/Soccer-Players-16/data.yaml, epochs=5, patience=50, batch=16, imgsz=640, save=True, cache=False, device=, workers=8, project=None, name=None, exist_ok=False, pretrained=False, optimizer=SGD, verbose=True, seed=0, deterministic=True, single_cls=False, image_weights=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, overlap_mask=True, mask_ratio=4, dropout=False, val=True, save_json=False, save_hybrid=False, conf=0.001, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=ultralytics/assets/, show=False, save_txt=False, save_conf=False, save_crop=False, hide_labels=False, hide_conf=False, vid_stride=1, line_thickness=3, visualize=False, augment=False, agnostic_nms=False, classes=None, retina_masks=False, boxes=True, format=torchscript, keras=False, optimize=False, int8=False, dynamic=False, simplify=False, opset=17

In [24]:
predictions = model.predict(
   source=input,
   conf=0.25,
   save=True,
)

Ultralytics YOLOv8.0.25 🚀 Python-3.8.10 torch-1.13.1+cu116 CPU
Model summary (fused): 168 layers, 3006233 parameters, 0 gradients, 8.1 GFLOPs

0: 384x640 1: 384x640 2: 384x640 3: 384x640 4: 384x640 5: 384x640 6: 384x640 7: 384x640 8: 384x640 9: 384x640 10: 384x640 11: 384x640 12: 384x640 13: 384x640 14: 384x640 15: 384x640 16: 384x640 17: 384x640 18: 384x640 19: 384x640 20: 384x640 21: 384x640 22: 384x640 23: 384x640 24: 384x640 25: 384x640 26: 384x640 27: 384x640 28: 384x640 29: 384x640 30: 384x640 31: 384x640 32: 384x640 33: 384x640 34: 384x640 35: 384x640 36: 384x640 37: 384x640 38: 384x640 39: 384x640 40: 384x640 41: 384x640 42: 384x640 43: 384x640 44: 384x640 45: 384x640 46: 384x640 47: 384x640 48: 384x640 49: 384x640 50: 384x640 51: 384x640 52: 384x640 53: 384x640 54: 384x640 55: 384x640 56: 384x640 57: 384x640 58: 384x640 59: 384x640 60: 384x640 61: 384x640 62: 384x640 63: 384x640 64: 384x640 65: 384x640 66: 384x640 67: 384x640 68: 384x640 69: 384x640 70: 384x640 71: 384x640 72:

In [25]:
(
    ffmpeg
    .input('runs/detect/predict/image%d.jpg', framerate=29.98)
    .output('prediction.mp4')
    .run()
)

(None, None)

In [26]:
from IPython.display import HTML
from base64 import b64encode
mp4 = open('prediction.mp4','rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=700 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)